In [8]:
%pwd

'/Users/kiebot/my-work/carely-companion-chatbot/research'

In [10]:
import os
os.chdir('../')

In [12]:
%pwd

'/Users/kiebot/my-work/carely-companion-chatbot'

In [1]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.document_loaders import UnstructuredPDFLoader

In [126]:
def load_pdf_file(folder_path):
    loader = DirectoryLoader(folder_path, glob="*.pdf", loader_cls=PyPDFLoader)

    documents = loader.load()

    return documents

In [127]:
def load_pdf_file_unstructured(folder_path):
    loader = DirectoryLoader(folder_path, glob="*.pdf", loader_cls=UnstructuredPDFLoader)
    documents = loader.load()
    return documents

In [128]:
extracted_data = load_pdf_file(folder_path='data/')

# extracted_data = load_pdf_file_unstructured(folder_path='data/')

In [129]:
extracted_data

[Document(metadata={'producer': 'iLovePDF', 'creator': 'PyPDF', 'creationdate': '', 'moddate': '2020-12-26T12:25:18+00:00', 'source': 'data/medical_diagnosis.pdf', 'total_pages': 147, 'page': 0, 'page_label': '1'}, page_content='Editor\nProf. Dr. Sıddık Keskin\nMedical Diagnosis\nand\nTreatment Methods\nin\nBasic Medical Sciences\nMedical Diagnosis and Treatment Methods in Basic Medical Sciences\nHealth\nlivredelyon.com\nlivredelyon\nlivredelyon\nlivredelyon\nISBN: 978-2-38236-061-3'),
 Document(metadata={'producer': 'iLovePDF', 'creator': 'PyPDF', 'creationdate': '', 'moddate': '2020-12-26T12:25:18+00:00', 'source': 'data/medical_diagnosis.pdf', 'total_pages': 147, 'page': 1, 'page_label': '2'}, page_content='Medical Diagnosis and Treatment Methods  \nin  \nBasic Medical Sciences \n \n \n \n \n \nEditor \nProf. Dr. Sıddık Keskin \n \n \n \n \nLyon 2020'),
 Document(metadata={'producer': 'iLovePDF', 'creator': 'PyPDF', 'creationdate': '', 'moddate': '2020-12-26T12:25:18+00:00', 'source

In [130]:
# Split the data into Text chunks

def text_split(ed):
    text_splitter=RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
    text_chunks = text_splitter.split_documents(ed)
    return text_chunks

In [131]:
text_chunks = text_split(ed=extracted_data)


print("text_chunks", len(text_chunks))

text_chunks 55330


In [132]:
from langchain.embeddings import  HuggingFaceEmbeddings

def download_hugging_face_embeddings():
    embeddings = HuggingFaceEmbeddings(model_name='sentence-transformers/all-MiniLM-L6-v2')
    return embeddings

In [133]:
embeddings = download_hugging_face_embeddings()

In [48]:
query_result = embeddings.embed_query('Hello word')
print('len', len(query_result))

len 384


In [49]:
query_result

[-0.022057348862290382,
 0.03135433793067932,
 0.04234996438026428,
 0.026110908016562462,
 -0.06519314646720886,
 -0.07004161924123764,
 0.054308973252773285,
 -0.001613021595403552,
 -0.06259442120790482,
 0.035306110978126526,
 0.027306020259857178,
 0.05138076841831207,
 0.09750930964946747,
 -0.06328082084655762,
 0.008590334095060825,
 0.022969508543610573,
 0.0637909322977066,
 -0.026898588985204697,
 -0.13075023889541626,
 0.039458081126213074,
 -0.047593604773283005,
 0.05164394900202751,
 -0.008419306948781013,
 0.0008068043389357626,
 -0.02593022584915161,
 -0.011951669119298458,
 -0.015885166823863983,
 0.01577826403081417,
 0.047061238437891006,
 -0.07030079513788223,
 0.05021481588482857,
 0.020775921642780304,
 0.13571418821811676,
 0.02362969145178795,
 0.01985788531601429,
 0.03593345358967781,
 -0.04672626033425331,
 -0.06226659193634987,
 -0.013844907283782959,
 -0.012370138429105282,
 -0.031761039048433304,
 -0.09367706626653671,
 -0.03493386507034302,
 -0.025743622

In [122]:
from dotenv import load_dotenv
load_dotenv()

True

In [123]:
import os

PINECONE_API_KEY = os.environ.get('PINECONE_API_KEY')
INDEX_NAME = os.environ.get('INDEX_NAME')
GEN_AI_API_KEY = os.environ.get('GEN_AI_API_KEY')

In [124]:
import os
os.environ["OPEN_AI_API_KEY"] = OPEN_AI_API_KEY
os.environ["PINECONE_API_KEY"] = PINECONE_API_KEY

In [125]:
from pinecone.grpc import PineconeGRPC as Pinecone
from pinecone import ServerlessSpec

pc = Pinecone(api_key=PINECONE_API_KEY)

index_name = INDEX_NAME

pc.create_index(
    name=index_name,
    dimension=384,
    metric='cosine',
    spec=ServerlessSpec(
        cloud='aws',
        region='us-east-1'
    )
)

PineconeApiException: (409)
Reason: Conflict
HTTP response headers: HTTPHeaderDict({'content-type': 'text/plain; charset=utf-8', 'access-control-allow-origin': '*', 'vary': 'origin,access-control-request-method,access-control-request-headers', 'access-control-expose-headers': '*', 'x-pinecone-api-version': '2025-04', 'x-cloud-trace-context': '38e69fc650ffc3dc67d2c56ed5abe146', 'date': 'Fri, 23 May 2025 18:40:53 GMT', 'server': 'Google Frontend', 'Content-Length': '85', 'Via': '1.1 google', 'Alt-Svc': 'h3=":443"; ma=2592000,h3-29=":443"; ma=2592000'})
HTTP response body: {"error":{"code":"ALREADY_EXISTS","message":"Resource  already exists"},"status":409}


In [55]:
from langchain_pinecone import PineconeVectorStore

doc_search = PineconeVectorStore.from_documents(
    documents=text_chunks,
    index_name=index_name,
    embedding=embeddings
)

In [57]:
from langchain_pinecone import PineconeVectorStore

doc_search = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embeddings
)

In [58]:
doc_search

In [116]:
retriever = doc_search.as_retriever(search_type='similarity', search_kwargs={"k": 3})

In [117]:
retriever_docs = retriever.invoke("What is Acne?")

In [61]:
retriever_docs

[Document(id='25637582-b05f-4aac-9c94-ceb44994d461', metadata={'creationdate': '2004-12-18T17:00:02-05:00', 'creator': 'PyPDF', 'moddate': '2004-12-18T16:15:31-06:00', 'page': 39.0, 'page_label': '40', 'producer': 'PDFlib+PDI 5.0.0 (SunOS)', 'source': 'data/Medical_book.pdf', 'total_pages': 637.0}, page_content='GALE ENCYCLOPEDIA OF MEDICINE 226\nAcne\nGEM - 0001 to 0432 - A  10/22/03 1:41 PM  Page 26'),
 Document(id='ac75c84e-b395-4d72-885f-c2ead567bf6c', metadata={'creationdate': '2004-12-18T17:00:02-05:00', 'creator': 'PyPDF', 'moddate': '2004-12-18T16:15:31-06:00', 'page': 38.0, 'page_label': '39', 'producer': 'PDFlib+PDI 5.0.0 (SunOS)', 'source': 'data/Medical_book.pdf', 'total_pages': 637.0}, page_content='GALE ENCYCLOPEDIA OF MEDICINE 2 25\nAcne\nAcne vulgaris affecting a woman’s face. Acne is the general\nname given to a skin disorder in which the sebaceous\nglands become inflamed. (Photograph by Biophoto Associ-\nates, Photo Researchers, Inc. Reproduced by permission.)\nGEM - 

In [93]:
from langchain_openai import OpenAI
from langchain_google_genai import GoogleGenerativeAI

llm = GoogleGenerativeAI(
    model="gemini-1.5-flash",  # or another Gemini model name if desired
    google_api_key=GEN_AI_API_KEY,
    temperature=0.4,
    max_output_tokens=500
)

In [94]:
llm

GoogleGenerativeAI(model='gemini-1.5-flash', google_api_key=SecretStr('**********'), temperature=0.4, max_output_tokens=500, client=ChatGoogleGenerativeAI(model='models/gemini-1.5-flash', google_api_key=SecretStr('**********'), temperature=0.4, max_output_tokens=500, client=<google.ai.generativelanguage_v1beta.services.generative_service.client.GenerativeServiceClient object at 0x300ed48a0>, default_metadata=(), model_kwargs={}))

In [97]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

system_prompt = (
    "You are an assistant for questions answering tasks. "
    "Use the following pieces of retrieved context to answer "
    "the question if you dont know the answer, say that you dont know, use three sentence max and keep the "
    "answer concise."
    "\n\n"
    "{context}"
)

prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_prompt),
        ("human", "{input}")
    ]
)

In [118]:
question_answer_chain = create_stuff_documents_chain(llm=llm, prompt=prompt)
rag_chain = create_retrieval_chain(retriever, question_answer_chain)

In [114]:
response = rag_chain.invoke({"input": "I have lot of pimple in face why"})

In [115]:
print("response", response["answer"])

response Several factors contribute to acne, including excess sebum production, clogged pores, and bacteria.  A balanced diet, stress reduction, and proper hygiene (like washing your hair frequently) can help.  Picking or squeezing pimples should be avoided.
